<a href="https://colab.research.google.com/github/bahramzada/az-ner-blur/blob/main/Untitled5.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import requests
from bs4 import BeautifulSoup

BASE_URL = "https://apa.az/all-news?page={}"
HEADERS = {
    "User-Agent": "Mozilla/5.0"
}

def get_news_links(page_num):
    url = BASE_URL.format(page_num)
    resp = requests.get(url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    # Xəbər linklərini tap (href-ləri .news-item və ya uyğun class ilə seç)
    links = []
    for a in soup.select('a.news-item, a.card-news, a[href^="/az/news/"]'):
        href = a.get('href')
        if href and href.startswith('/'):
            links.append('https://apa.az' + href)
    return links

def scrape_news(news_url):
    resp = requests.get(news_url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    # Başlığı tap
    title_tag = soup.find('h2', class_="title_news mb-site")
    title = title_tag.text.strip() if title_tag else ""
    # İlk paraqrafı tap
    p_tag = soup.find('p')
    paragraph = p_tag.text.strip() if p_tag else ""
    return {"url": news_url, "title": title, "paragraph": paragraph}

if __name__ == "__main__":
    for page in range(1, 3):  # Səhifə sayını artırmaq üçün 3-ü dəyişin
        links = get_news_links(page)
        for link in links:
            news = scrape_news(link)
            print(f"URL: {news['url']}")
            print(f"Başlıq: {news['title']}")
            print(f"Paraqraf: {news['paragraph']}\n{'-'*60}")

In [ ]:
import requests
from bs4 import BeautifulSoup
import time

BASE_URL = "https://apa.az/all-news?page={}"
HEADERS = {"User-Agent": "Mozilla/5.0"}

def get_news_links(page_num):
    page_url = BASE_URL.format(page_num)
    resp = requests.get(page_url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    links = []
    for a in soup.select('a.item'):
        href = a.get('href')
        if href.startswith('/'):
            full_url = 'https://apa.az' + href
        else:
            full_url = href
        links.append(full_url)
    return links

def scrape_news(news_url):
    resp = requests.get(news_url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    title_tag = soup.find('h2', class_="title_news mb-site")
    title = title_tag.text.strip() if title_tag else ""

    # Bütün paraqrafları <div class="texts mb-site" itemprop="articleBody"> içərisindən götür
    texts_div = soup.find('div', class_="texts mb-site", itemprop="articleBody")
    if texts_div:
        paragraphs = [p.get_text(separator=' ', strip=True) for p in texts_div.find_all('p')]
        # Bir neçə paraqraf varsa, birləşdir
        full_text = "\n\n".join(paragraphs)
    else:
        full_text = ""
    return {
        "url": news_url,
        "title": title,
        "text": full_text
    }

if __name__ == "__main__":
    all_news = []
    for page in range(1, 4):  # Səhifə 1, 2, 3
        print(f"==== Səhifə {page} ====")
        links = get_news_links(page)
        for link in links:
            try:
                news = scrape_news(link)
                print(news)
                all_news.append(news)
                time.sleep(1)  # Saytı qorumaq üçün gecikmə
            except Exception as e:
                print(f"Xəta: {e} link: {link}")

    # Nəticəni JSON-a yazmaq üçün aşağıdakıları əlavə edə bilərsiniz:
    # import json
    # with open("apa_all_news_texts.json", "w", encoding="utf-8") as f:
    #     json.dump(all_news, f, ensure_ascii=False, indent=2)

==== Səhifə 1 ====
{'url': 'https://apa.az/rates', 'title': '', 'text': ''}
{'url': 'https://apa.az/weather-forecast', 'title': '', 'text': ''}
{'url': 'https://apa.az/rates', 'title': '', 'text': ''}
{'url': 'https://apa.az/weather-forecast', 'title': '', 'text': ''}
{'url': 'https://apa.az/avropa/zelenski-ukrayna-ordusu-ruslarin-sumiya-hucum-emeliyyatini-tamamile-puca-cixarib-916613', 'title': 'Zelenski: Ukrayna ordusu rusların Sumıya hücum əməliyyatını tamamilə puça çıxarıb', 'text': 'Ukrayna Silahlı Qüvvələri Rusiyanın Sumıya qarşı hücum əməliyyatını tamamilə puça çıxarıb. Düşmən böyük itkilər verib.\n\nAPA "RBK-Ukrayna"ya istinadən xəbər verir ki, bunu Ukrayna Prezidenti Volodimir Zelenski bildirib.\n\nDövlət başçısının sözlərinə görə, bu gün o, Ali Baş Komandanın qərargahının çox əhatəli iclasını keçirib. Görüşdə hava hücumundan müdafiə sistemləri və onlara raketlərin tədarükü, Ukrayna ordusunun ehtiyacları və mövcud müdafiə resursları müzakirə olunub.\n\n“Partnyorlarla işin daha

KeyboardInterrupt: 

In [ ]:
import requests
from bs4 import BeautifulSoup
import time

BASE_URL = "https://apa.az/all-news?page={}"
HEADERS = {"User-Agent": "Mozilla/5.0"}

def get_news_links(page_num):
    page_url = BASE_URL.format(page_num)
    resp = requests.get(page_url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    links = []
    for a in soup.select('a.item'):
        href = a.get('href')
        # Yalnız xəbər linkləri ("/rates", "/weather-forecast" və s. atılır)
        if not href or any(x in href for x in ["/rates", "/weather-forecast"]):
            continue
        # Tam link düzəlt
        full_url = 'https://apa.az' + href if href.startswith('/') else href
        links.append(full_url)
    return links

def scrape_news(news_url):
    resp = requests.get(news_url, headers=HEADERS)
    soup = BeautifulSoup(resp.text, "html.parser")
    title_tag = soup.find('h2', class_="title_news mb-site")
    title = title_tag.text.strip() if title_tag else ""
    # Məqalə mətni: texts mb-site
    texts_div = soup.find('div', class_="texts mb-site", itemprop="articleBody")
    if texts_div:
        paragraphs = [p.get_text(separator=' ', strip=True) for p in texts_div.find_all('p')]
        full_text = "\n\n".join(paragraphs)
    else:
        full_text = ""
    return {
        "url": news_url,
        "title": title,
        "text": full_text
    }

if __name__ == "__main__":
    all_news = []
    for page in range(1, 161):  # 3 səhifə
        print(f"==== Səhifə {page} ====")
        links = get_news_links(page)
        for link in links:
            try:
                news = scrape_news(link)
                print(news)
                all_news.append(news)
                time.sleep(0.3)
            except Exception as e:
                print(f"Xəta: {e} link: {link}")

    # JSON faylına yazmaq üçün:
    import json
    with open("apa_all_news_texts.json", "w", encoding="utf-8") as f:
        json.dump(all_news, f, ensure_ascii=False, indent=2)

==== Səhifə 1 ====
{'url': 'https://apa.az/avropa/ai-rusiyaya-qarsi-sanksiyalari-6-ay-uzadib-916615', 'title': 'Aİ Rusiyaya qarşı sanksiyaları 6 ay uzadıb', 'text': 'Avropa İttifaqı Rusiyaya qarşı bütün sanksiyalar paketinin müddətini daha altı ay uzadıb.\n\nAPA xəbər verir ki, bu barədə Aİ Şurası məlumat yayıb. Məlumata görə, məhdudiyyətlər 2026-cı il martın 15-dək qüvvədə qalacaq.\n\n“Bu gün Şura qərara aldı ki, məhdudlaşdırıcı tədbirlər daha 6 ay, yəni 2026-cı il martın 15-dək uzadılsın”, – açıqlamada deyilir. Qeyd olunur ki, sanksiyalar əvvəlki kimi 2 500-dən çox fiziki və hüquqi şəxsə şamil olunacaq.'}
{'url': 'https://apa.az/avropa/zelenski-ukrayna-ordusu-ruslarin-sumiya-hucum-emeliyyatini-tamamile-puca-cixarib-916613', 'title': 'Zelenski: Ukrayna ordusu rusların Sumıya hücum əməliyyatını tamamilə puça çıxarıb', 'text': 'Ukrayna Silahlı Qüvvələri Rusiyanın Sumıya qarşı hücum əməliyyatını tamamilə puça çıxarıb. Düşmən böyük itkilər verib.\n\nAPA "RBK-Ukrayna"ya istinadən xəbər ver

In [ ]:
import pandas as pd

In [ ]:
df = pd.read_json('/content/apa_all_news_texts.json')

In [ ]:
df = df[['title','text']]

In [ ]:
df

title  \
0            Aİ Rusiyaya qarşı sanksiyaları 6 ay uzadıb   
1     Zelenski: Ukrayna ordusu rusların Sumıya hücum...   
2     Almaniya Polşa sərhədinə qırıcı təyyarələr gön...   
3     Azərbaycan ərazisinin Ermənistandan atəşə tutu...   
4     Belqorod və Bryansk üzərində dörd saata 16 PUA...   
...                                                 ...   
3834        Sabah Bakıda yağış yağacaq - SABAHIN HAVASI   
3835  Ceyhun Bayramovla Qazaxıstanın XİN rəhbəri ara...   
3836  Azərbaycan Hərbi Dəniz Qüvvələri Xəzərdə döyüş...   
3837  Azərbaycanın sərhəd buraxılış məntəqələrindən ...   
3838         Paytaxtda narkotik satan qardaşlar tutulub   

                                                   text  
0     Avropa İttifaqı Rusiyaya qarşı bütün sanksiyal...  
1     Ukrayna Silahlı Qüvvələri Rusiyanın Sumıya qar...  
2     Almaniya Polşa sərhədinə iki "Eurofighter" qır...  
3     Ermənistanın Azərbaycana qarşı hərbi təcavüzü ...  
4     Rusiya hava hücumundan müdafiə qüvvələri dörd ...  
...                                                 ...  
3834  Avqustun 15-də gözlənilən hava şəraiti açıqlan...  
3835  Avqustun 14-də Azərbaycan Respublikasının xari...  
3836  Cari ilin hazırlıq planına əsasən, Hərbi Dəniz...  
3837  Ötən il Azərbaycanın sərhəd buraxılış məntəqəl...  
3838  Paytaxtda narkotiklərin satışı ilə məşğul olan...  

[3839 rows x 2 columns]

In [ ]:
import pandas as pd
from datasets import Dataset
from transformers import MBartForConditionalGeneration, MBart50TokenizerFast, Trainer, TrainingArguments
import torch

# 1. Data loading
dataset = Dataset.from_pandas(df)

model_name = "facebook/mbart-large-50-many-to-many-mmt"
tokenizer = MBart50TokenizerFast.from_pretrained(model_name)
tokenizer.src_lang = "az_AZ"
tokenizer.tgt_lang = "az_AZ"
device = "cuda" if torch.cuda.is_available() else "cpu"
print(device)
def preprocess(data):
    inputs = data["text"]
    targets = data["title"]
    model_inputs = tokenizer(
        inputs,
        max_length=512,
        truncation=True,
        padding="max_length"
    )
    with tokenizer.as_target_tokenizer():
        labels = tokenizer(
            targets,
            max_length=64,
            truncation=True,
            padding="max_length"
        )
    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_dataset = dataset.map(preprocess, batched=True)

# Load the model
model = MBartForConditionalGeneration.from_pretrained(model_name)
model = model.to(device)

# 5. Training arguments -- 300 step, hər 50 stepdə log
training_args = TrainingArguments(
    output_dir="./az_mbart_summarizer",
    max_steps=300,                  # Cəmi 300 step
    logging_steps=50,               # Hər 50 stepdə log
    save_steps=50,                 # Hər 200 stepdə model saxla (istəyə görə dəyiş)
    learning_rate=2e-5,
    per_device_train_batch_size=2,
    save_total_limit=50,
    fp16=True,
    eval_strategy="no",
)

# 6. Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_dataset,
)

trainer.train()
model.save_pretrained("./az_mbart_summarizer")
tokenizer.save_pretrained("./az_mbart_summarizer")

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/529 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/649 [00:00<?, ?B/s]

config.json: 0.00B [00:00, ?B/s]

...

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize?ref=models
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: bahramzada (bahramzada-unec-business-school) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


/usr/local/lib/python3.12/dist-packages/transformers/modeling_utils.py:4034: UserWarning: Moving the following attributes in the config to the generation config: {'max_length': 200, 'early_stopping': True, 'num_beams': 5}. You are seeing this warning because you've set generation parameters in the model config, as opposed to in the generation config.
  warnings.warn(


('./az_mbart_summarizer/tokenizer_config.json',
 './az_mbart_summarizer/special_tokens_map.json',
 './az_mbart_summarizer/sentencepiece.bpe.model',
 './az_mbart_summarizer/added_tokens.json',
 './az_mbart_summarizer/tokenizer.json')

In [ ]:
from transformers import MBartForConditionalGeneration, MBart50TokenizerFast

# Model və tokenizer yüklə
model_name = "./az_mbart_summarizer"  # Əgər özün saxlamısansa
tokenizer = MBart50TokenizerFast.from_pretrained(model_name)
model = MBartForConditionalGeneration.from_pretrained(model_name)

# Test xəbəri
text = "Fövqəladə Hallar Nazirliyinin “112” qaynar telefon xəttinə Abşeron rayonu, Mehdiabad qəsəbəsi ərazisində yeddimərtəbəli yaşayış binasında yanğın baş verməsi barədə məlumat daxil olub və dərhal əraziyə Dövlət Yanğından Mühafizə Xidmətinin qüvvələri cəlb edilib."
# Tokenize et
inputs = tokenizer(
    text,
    return_tensors="pt",
    max_length=512,
    truncation=True
)
input_ids = inputs["input_ids"]

# Modeli GPU-ya göndər (əgər GPU varsa)
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"
model = model.to(device)
input_ids = input_ids.to(device)

# Xülasə (title) generasiya et
output = model.generate(
    input_ids,
    max_length=64,
    num_beams=4,
    forced_bos_token_id=tokenizer.lang_code_to_id["az_AZ"]
)
summary = tokenizer.decode(output[0], skip_special_tokens=True)
print("Generated title:", summary)

Generated title: Dövlət Yanğından Mühafizə qüvvələri cəlb edilib
